In [29]:
%reload_ext autoreload
%autoreload 2

import pandas as pd
pd.options.plotting.backend = "plotly"

import sys
sys.path.insert(0, 'driftpy/src/')

import driftpy
print(driftpy.__file__)

import numpy as np 
from sim.sim import DriftSim, SimpleDriftSim, load_hist_oracle

import os
import datetime
from sim.agents import * 
from programs.clearing_house.state import * 
from sim.events import OpenPositionEvent
from sim.helpers import random_walk_oracle, rand_heterosk_oracle, class_to_json
import pickle as cPickle

/Users/brennan/Documents/drift/simulation/drift-sim/driftpy/src/driftpy/__init__.py


In [30]:
def make_clearing_house(
    base_spread, 
    oracle=None,
):
    # generate random oracle data 
    if oracle is None: 
        prices, timestamps = random_walk_oracle(1)
        oracle = Oracle(prices=prices, timestamps=timestamps)
    
    # create the market with/without spread 
    amm = AMM(
        oracle=oracle, 
        base_asset_reserve=int(10_000_000 * AMM_RESERVE_PRECISION), 
        quote_asset_reserve=int(10_000_000 * AMM_RESERVE_PRECISION),
        funding_period=60*60,
        peg_multiplier=int(oracle.get_price(0) * PEG_PRECISION),
        base_spread=base_spread
    )
    market = Market(amm)
        
    # create clearing house 
    fee_structure = FeeStructure(numerator=1, denominator=1000)
    clearing_house = ClearingHouse([market], fee_structure)
    clearing_house.name = f''

    return clearing_house
    
# agent which always pushes mark => oracle 
arb = Arb(
    intensity=0.8, 
    market_index=0, 
    user_index=0,
)

# random trader 
noise = Noise(
    intensity=1, 
    market_index=0, 
    user_index=0,
    size=1_000, # 1k trades
)

lp = LP(
    lp_start_time=0, 
    lp_duration=300, 
    deposit_amount=1_000 * QUOTE_PRECISION, 
    user_index=1, 
    market_index=0,
)

agents = [
    arb,
    noise,
    lp,
]
os.makedirs("sim-results/", exist_ok=True)

In [31]:
sim = SimpleDriftSim(
    "sim-results/lp",
    clearing_house=make_clearing_house(base_spread=0),
    agents=agents
)

sim.run()
results = sim.to_df(save=True)
results.head()

running simulation for 515 timesteps
running sim from timestamp 0 to 515
skipping time step: 0 ... ch time: 4
skipping time step: 1 ... ch time: 4
skipping time step: 2 ... ch time: 4
skipping time step: 3 ... ch time: 4
1000000000
NOW:  5
short 1681810.077708 LUNA-PERP @ 4.644818992229171 ( 4.4825147456 )
5 1 300
NOW:  6
short 344068.371469 LUNA-PERP @ 4.449310189056723 ( 4.4163515977 )
6 2 300
NOW:  7
short 69191.43796 LUNA-PERP @ 4.409723693137371 ( 4.4031057355 )
7 3 300
NOW:  8
short 13864.623675 LUNA-PERP @ 4.401779625003771 ( 4.4004539139 )
8 4 300
NOW:  9
short 2776.199591 LUNA-PERP @ 4.400188458541435 ( 4.3999230192 )
9 5 300
NOW:  10
short 555.815181 LUNA-PERP @ 4.399869876330149 ( 4.3998167341 )
10 6 300
NOW:  11
short 111.275126 LUNA-PERP @ 4.399806095071443 ( 4.3997954558 )
11 7 300
12 8 300
13 9 300
NOW:  14
short 1410503.483248 LUNA-PERP @ 4.264935666889038 ( 4.1342095162 )
14 10 300
NOW:  15
short 4234201.510446 LUNA-PERP @ 3.7417816553146213 ( 3.3866038722 )
15 11 300


NOW:  152
long 2938.541869 LUNA-PERP @ 8.926823155742419 ( 8.9272233604 )
152 148 300
NOW:  153
long 587.10487 LUNA-PERP @ 8.927303319092458 ( 8.9273832786 )
153 149 300
NOW:  154
long 138772.83307 LUNA-PERP @ 8.94628313977168 ( 8.9652230132 )
154 150 300
NOW:  155
long 27691.687162 LUNA-PERP @ 8.969002406026966 ( 8.9727833921 )
155 151 300
NOW:  156
long 5531.400571 LUNA-PERP @ 8.973538642161193 ( 8.9742939558 )
156 152 300
NOW:  157
long 1105.118301 LUNA-PERP @ 8.974444859888719 ( 8.9745957665 )
157 153 300
NOW:  158
long 220.80049 LUNA-PERP @ 8.974625917361115 ( 8.9746560683 )
158 154 300
NOW:  159
long 44.11585 LUNA-PERP @ 8.974662092846197 ( 8.9746681166 )
159 155 300
NOW:  160
long 8.814159 LUNA-PERP @ 8.974669323510309 ( 8.9746705238 )
160 156 300
NOW:  161
short 160019.937162 LUNA-PERP @ 8.952819317282344 ( 8.9310213133 )
161 157 300
NOW:  162
short 32082.936684 LUNA-PERP @ 8.926650957995092 ( 8.9222827413 )
162 158 300
NOW:  163
short 6424.891135 LUNA-PERP @ 8.921407967370193 

278 274 300
NOW:  279
long 48.444408 LUNA-PERP @ 13.342408396206448 ( 13.3424164627 )
279 275 300
NOW:  280
long 9.679388 LUNA-PERP @ 13.34241807694556 ( 13.3424196859 )
280 276 300
NOW:  281
long 1756376.209002 LUNA-PERP @ 13.634853045420751 ( 13.9336958323 )
281 277 300
NOW:  282
long 346427.999357 LUNA-PERP @ 13.992639644138356 ( 14.0518328064 )
282 278 300
NOW:  283
long 69041.546571 LUNA-PERP @ 14.06362973816202 ( 14.0754365738 )
283 279 300
NOW:  284
long 13787.56054 LUNA-PERP @ 14.077794392669135 ( 14.0801526065 )
284 280 300
NOW:  285
long 2754.478017 LUNA-PERP @ 14.080623730273272 ( 14.0810948699 )
285 281 300
NOW:  286
long 550.333582 LUNA-PERP @ 14.08118900163638 ( 14.0812831341 )
286 282 300
NOW:  287
long 109.956246 LUNA-PERP @ 14.081301942578005 ( 14.0813207493 )
287 283 300
NOW:  288
short 133271.307779 LUNA-PERP @ 14.05852518097953 ( 14.0357665153 )
288 284 300
NOW:  289
short 26706.886221 LUNA-PERP @ 14.03120579547885 ( 14.0266465576 )
289 285 300
NOW:  290
short 5347.

405 401 300
NOW:  406
long 9218439.030277 LUNA-PERP @ 16.01077062541845 ( 17.7827081582 )
406 402 300
NOW:  407
long 9218439.030277 LUNA-PERP @ 16.01077062541845 ( 17.7827081582 )
407 403 300
NOW:  408
long 9218439.030277 LUNA-PERP @ 16.01077062541845 ( 17.7827081582 )
408 404 300
NOW:  409
long 9360357.402875 LUNA-PERP @ 16.035331508445108 ( 17.8373081552 )
409 405 300
NOW:  410
long 9360357.402875 LUNA-PERP @ 16.035331508445108 ( 17.8373081552 )
410 406 300
NOW:  411
long 9360357.402875 LUNA-PERP @ 16.035331508445108 ( 17.8373081552 )
411 407 300
NOW:  412
long 9360357.402875 LUNA-PERP @ 16.035331508445108 ( 17.8373081552 )
412 408 300
NOW:  413
long 9360357.402875 LUNA-PERP @ 16.035331508445108 ( 17.8373081552 )
413 409 300
NOW:  414
long 9360357.402875 LUNA-PERP @ 16.035331508445108 ( 17.8373081552 )
414 410 300
NOW:  415
long 9360357.402875 LUNA-PERP @ 16.035331508445108 ( 17.8373081552 )
415 411 300
NOW:  416
long 9360357.402875 LUNA-PERP @ 16.035331508445108 ( 17.8373081552 )
41

100%|██████████████████████████████████| 1537/1537 [00:00<00:00, 3896.40it/s]


m0_mark_price  m0_oracle_price  m0_bid_price  m0_ask_price  m0_wouldbe_peg  \
0          4.813         4.813168         4.813         4.813           4.813   
1          4.813         4.813168         4.813         4.813           4.813   
2          4.813         4.813168         4.813         4.813           4.813   
3          4.813         4.813168         4.813         4.813           4.813   
4          4.813         4.813168         4.813         4.813           4.813   

   m0_wouldbe_peg_cost  m0_predicted_long_funding  m0_predicted_short_funding  \
0                  0.0              -1.456353e-08               -1.456353e-08   
1                  0.0              -1.456353e-08               -1.456353e-08   
2                  0.0              -1.456353e-08               -1.456353e-08   
3                  0.0              -1.456353e-08               -1.456353e-08   
4                  0.0              -1.456353e-08               -1.456353e-08   

   m0_last_mid_price_twap  m0_repeg_to_oracle_cost  ...  \
0                   4.813                      0.0  ...   
1                   4.813                      0.0  ...   
2                   4.813                      0.0  ...   
3                   4.813                      0.0  ...   
4                   4.813                      0.0  ...   

   u0_m0_last_cumulative_funding_rate  u0_m0_last_funding_rate_ts  u0_m0_upnl  \
0                                 NaN                         NaN         NaN   
1                                 NaN                         NaN         NaN   
2                                 NaN                         NaN         NaN   
3                                 NaN                         NaN         NaN   
4                                 NaN                         NaN         NaN   

   u0_m0_ufunding  u1_m0_base_asset_amount  u1_m0_quote_asset_amount  \
0             NaN                      NaN                       NaN   
1             NaN                      NaN                       NaN   
2             NaN                      NaN                       NaN   
3             NaN                      NaN                       NaN   
4             NaN                      NaN                       NaN   

   u1_m0_last_cumulative_funding_rate  u1_m0_last_funding_rate_ts  u1_m0_upnl  \
0                                 NaN                         NaN         NaN   
1                                 NaN                         NaN         NaN   
2                                 NaN                         NaN         NaN   
3                                 NaN                         NaN         NaN   
4                                 NaN                         NaN         NaN   

   u1_m0_ufunding  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  

[5 rows x 99 columns]

In [26]:
keep_columns = [c for c in results.columns if results[c].dtype == float or results[c].dtype == int]
filtered_df = results[keep_columns]
filtered_df.plot()